In [18]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score
import csv

In [19]:
train = pd.concat([pd.read_csv(f"data/comp_datasets_train/region_{i}_train.csv", index_col="date") for i in 'ABCDE'], axis=1)
test = pd.concat([pd.read_csv(f"data/comp_datasets_test/region_{i}_test.csv", index_col="date") for i in 'ABCDE'], axis=1)
solution_train = pd.read_csv("data/comp_datasets_train/solution_train.csv", index_col="date")

train = train.join(solution_train)

In [3]:
cols_to_delete = ['max.wind.speed.dir', 'max.inst.wind.speed.dir', 'min.atmos.pressure']
train = train.drop(columns=cols_to_delete)
test = test.drop(columns=cols_to_delete)

In [4]:
X_train, X_val, y_train, y_val = train_test_split(train.drop('label', axis=1), train['label'], test_size=0.2, random_state=42)

In [5]:
model = RandomForestClassifier(n_estimators=300, max_depth=20, min_samples_split=10, min_samples_leaf=2,random_state=42)
model.fit(X_train, y_train)

RandomForestClassifier(max_depth=20, min_samples_leaf=2, min_samples_split=10,
                       n_estimators=300, random_state=42)

In [6]:
predictions = model.predict(test)

In [7]:
X_val, X_test, y_val, y_test = train_test_split(X_val, y_val, test_size=0.5, random_state=42)

In [8]:
test_predictions = model.predict(X_test)

In [9]:
accuracy = accuracy_score(y_test, test_predictions)

In [10]:
print(f"Test Accuracy: {accuracy * 100:.2f}%")

Test Accuracy: 64.91%


In [11]:
# DO NOT EXECUTE AFTER THIS POINT IF YOU DON'T WANT TO SAVE THE PREDICTIONS

In [12]:
label_mapping = {0: 'H', 1: 'L', 2: 'N'}

In [13]:
train['label'] = train['label'].replace(label_mapping)
predictions = pd.Series(predictions).replace(label_mapping).values

In [14]:
pd.DataFrame(predictions, index=test.index, columns=['label']).to_csv('data/comp_datasets_train/solution_format.csv', quoting=csv.QUOTE_ALL)

In [15]:
import matplotlib.pyplot as plt

# Assuming 'train' DataFrame contains the actual data and 'predictions' variable contains the predicted data
actual = train['label']
predicted = predictions

plt.figure(figsize=(500, 70))

# Plotting the actual data
plt.plot(actual, label='Actual')

# Plotting the predicted data
plt.plot(predicted, label='Predicted', linestyle='--')

plt.title('Actual vs Predicted')
plt.xlabel('Index')
plt.ylabel('Label')
plt.legend(loc='upper left')

# Set the limits of x and y axes
plt.xlim([0, 550])  # replace xmin and xmax with the desired values
plt.ylim([0, 3])  # replace ymin and ymax with the desired values

plt.show()